# Balanceamento Estrutural

Importando bibliotecas:

In [1]:
import sys
sys.path.append('..')
import networkx as nx
import socnet as sn
import numpy as np
import pandas as pd
from scipy import stats

from random import choice, random
from itertools import combinations

Configurando bibliotecas:

In [2]:
sn.node_size = 5
sn.node_color = (255, 255, 255)

sn.edge_width = 1

Definindo constantes:

In [3]:
NUM_NODES = 15

POSITIVE_COLOR = (0, 0, 255)
NEGATIVE_COLOR = (255, 0, 0)

Inicialização da simulação:

In [4]:
def set_edge_color(g, n, m):
    if g.edges[n, m]['signal'] == 1:
        g.edges[n, m]['color'] = POSITIVE_COLOR
    else:
        g.edges[n, m]['color'] = NEGATIVE_COLOR


def build_graph(frac_positives=0.5):
    g = nx.complete_graph(NUM_NODES)

    sn.reset_node_colors(g)

    for n, m in g.edges:
        if random() < frac_positives:
            g.edges[n, m]['signal'] = 1
        else:
            g.edges[n, m]['signal'] = -1

        set_edge_color(g, n, m)

    sn.reset_positions(g)

    return g

Passo da simulação:

In [5]:
def invert(g, n, m):
    g.edges[n, m]['signal'] *= -1

    set_edge_color(g, n, m)


def update(g, mec2_weight=1, mec3_weight=1, mec5_weight=1):
    # Inicializa as pressões.

    for n, m in g.edges():
        g.edges[n, m]['pressure'] = 0

    # Para cada tríade.
    for t in combinations(g.nodes, 3):
        # Lista todas as arestas da tríade.
        edges = [(t[0], t[1]), (t[0], t[2]), (t[1], t[2])]

        # Conta quantas arestas são positivas.
        num_positives = sum(g.edges[n, m]['signal'] == 1 for n, m in edges)

        # Duas positivas significa tríade instável.
        if num_positives == 2:
            for n, m in edges:
                if g.edges[n, m]['signal'] == -1:
                    g.edges[n, m]['pressure'] += mec2_weight # Mecanismo 2
                else:
                    g.edges[n, m]['pressure'] += mec3_weight # Mecanismo 3

        # Zero positivas também significa tríade instável.
        elif num_positives == 0:
            for n, m in edges:
                g.edges[n, m]['pressure'] += mec5_weight # Mecanismo 5
    # Obtém a maior pressão.
    pressure = max(g.edges[n, m]['pressure'] for n, m in g.edges)

    # Se for positiva, inverte uma aresta que esteja
    # sob essa pressão, escolhida aleatoriamente, e
    # devolve True para indicar que houve mudança.
    if pressure > 0:
        n, m = choice([(n, m) for n, m in g.edges if g.edges[n, m]['pressure'] == pressure])
        invert(g, n, m)
        return True

    # Se for zero, devolvendo False para indicar que
    # não houve mudança, ou seja, a rede estabilizou.
    return False

Animação da simulação:

In [6]:
g = build_graph()

sn.reset_positions(g)

frames = []

while update(g):
    sn.update_positions(g, weight='signal')

    frames.append(sn.generate_frame(g))

print('simulação encerrada, gerando animação...')

sn.show_animation(frames)

simulação encerrada, gerando animação...


Avaliação da simulação:

In [7]:
def number_components(g):
    h = g.copy()

    for n, m in g.edges:
        if g.edges[n, m]['signal'] == -1:
            h.remove_edge(n, m)

    return nx.number_connected_components(h)


#print(number_components(g))

In [8]:
def simulater(frac_pos=0.5, weight2=1, weight5=1):
    g = build_graph(frac_pos)
    sn.reset_positions(g)

    frames = []
    k = 0
    while update(g, mec2_weight = weight2, mec5_weight = weight5):
        k += 1
        sn.update_positions(g, weight='signal')
        frames.append(sn.generate_frame(g))
        if k == 50:
            break
    return number_components(g)

#### * Conforme a proporção inicial de amizades aumenta, a quantidade final de componentes diminui.

#### * Conforme o peso das pressões positivas (Mecanismo 2 e Mecanismo 5) aumenta em relação ao peso das pressões negativas (Mecanismo 3), a quantidade final de componentes diminui.

### Objetivo 3
Você deve operacionalizar e testar as hipóteses acima e entregá-las como um
notebook organizado e compreensível. Lembre que:

* a distribuição inicial de amizades e inimizades é aleatória, portanto você não pode afirmar que a quantidade de componentes mudou sem rodar várias simulações e fazer um teste-t;
* uma simulação pode não convergir, portanto você deve estabelecer um limite de iterações, por exemplo a partir da média da quantidade de iterações das simulações que terminam;
* as simulações em si podem demorar, então recomendamos dividir o trabalho em duas fases: preparem as simulações logo, deixem elas rodando enquanto trabalham em outras disciplinas e retomem quando terminarem.

In [9]:
bench_list = []
for i in range(100):
    bench_list.append(simulater())

In [20]:
frac_pos_list = [0.7, 0.75, 0.8, 0.85, 0.90, 0.95]
frac_components = []

for i in frac_pos_list:
    lista = []
    for j in range(100):
        lista.append(simulater(frac_pos=i))
    frac_components.append(lista)

In [21]:
frac_comp_mean = []
for i in range(len(frac_components)):
    media = np.mean(frac_components[i])
    frac_comp_mean.append(media)

In [30]:
weight_list = [1.75, 2, 2.75, 3.5, 4.25, 5]
weight_components = []

for i in weight_list:
    lista = []
    for j in range(100):
        lista.append(simulater(weight2 = i, weight5 = i))
    weight_components.append(lista)

In [31]:
weight_comp_mean = []
for i in range(len(weight_components)):
    media = np.mean(weight_components[i])
    weight_comp_mean.append(media)

In [28]:
data_frac = pd.DataFrame({
    'Proporção inicial de amizades': frac_pos_list,
    'Média do número de componentes': frac_comp_mean,
    'P-value': [stats.ttest_ind(bench_list, n, equal_var=False)[1] for n in frac_components]
})
data_frac

Proporção inicial de amizades  Média do número de componentes  \
0                           0.70                            1.76   
1                           0.75                            1.30   
2                           0.80                            1.14   
3                           0.85                            1.02   
4                           0.90                            1.00   
5                           0.95                            1.00   

         P-value  
0   8.603638e-07  
1   1.981740e-27  
2   1.241611e-45  
3  1.654988e-115  
4  8.038310e-101  
5  8.038310e-101

In [32]:
data_weight = pd.DataFrame({
    'Peso das pressões positivas': weight_list,
    'Média do número de componentes': weight_comp_mean,
    'P-value': [stats.ttest_ind(bench_list, n, equal_var=False)[1] for n in weight_components]
})
data_weight

Peso das pressões positivas  Média do número de componentes        P-value
0                         1.75                            1.55   6.362302e-14
1                         2.00                            1.25   1.315329e-31
2                         2.75                            1.13   1.527574e-47
3                         3.50                            1.02  1.654988e-115
4                         4.25                            1.02  1.654988e-115
5                         5.00                            1.00  8.038310e-101

### Objetivo 4
Você deve analisar e interpretar os resultados das simulações. Usem, como sempre, o guia disponível em https://tinyurl.com/redesoc-2018 e o modelo disponível em Documentos/Modelo no Blackboard.